# Compactness Measures

© Metric Geometry and Gerrymandering Group 2018

This notebook encapsulates the calculation of various compactness measures.

In [52]:
import geopandas as gpd
import shapely as shp
import math
import numpy as np

from skimage.feature import corner_harris, corner_peaks
from sklearn.decomposition import PCA
from sklearn.preprocessing import scale

import plotly.plotly as py
import plotly.figure_factory as ff
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
import plotly.graph_objs as go

init_notebook_mode(connected=True)

In [2]:
from numpy import mean, absolute

# Stack Overflow <https://stackoverflow.com/questions/8930370/where-can-i-find-mad-mean-absolute-deviation-in-scipy>
def mad(data, axis=None):
    return mean(absolute(data - mean(data, axis)), axis)

### Load Data:

In [3]:
data_path = "../shapes/tl_2016_us_cd115.shp"
data = gpd.read_file(data_path)

In [4]:
data.head()

STATEFP CD115FP GEOID                           NAMELSAD LSAD CDSESSN  \
0      02      00  0200  Congressional District (at Large)   C1     115   
1      10      00  1000  Congressional District (at Large)   C1     115   
2      30      00  3000  Congressional District (at Large)   C1     115   
3      38      00  3800  Congressional District (at Large)   C1     115   
4      46      00  4600  Congressional District (at Large)   C1     115   

   MTFCC FUNCSTAT          ALAND        AWATER     INTPTLAT      INTPTLON  \
0  G5200        N  1477946266785  245390495931  +63.3461909  -152.8370690   
1  G5200        N     5047194742    1398720828  +38.9985380  -075.4416616   
2  G5200        N   376964956503    3866986696  +47.0511771  -109.6348174   
3  G5200        N   178711813026    4399093501  +47.4421698  -100.4608163   
4  G5200        N   196348407642    3380782733  +44.4467957  -100.2381762   

                                            geometry  
0  (POLYGON ((179.388742 51.941917, 179.404562 51...  
1  POLYGON ((-75.789023 39.65979, -75.788922 39.6...  
2  POLYGON ((-116.049116 48.000828, -116.049118 4...  
3  POLYGON ((-104.048967 48.86953399999999, -104....  
4  POLYGON ((-104.057879 44.997605, -104.050783 4...

In [5]:
test_geo = data.ix[0].geometry

### Utilities

In [6]:
def get_polygons(geometry):
    if type(geometry) is shp.geometry.polygon.Polygon:
        return [geometry]
    else:
        return [x for x in geometry]

In [7]:
def get_coords(geometry):
    polygons = get_polygons(geometry)
    return [coord for p in polygons for coord in p.exterior.coords]

In [8]:
# BUGGY -- NEEDS CORRECTION
def get_raster(geometry, scale_factor=1):
    minx, miny, maxx, maxy = geometry.bounds
    
    xspan = int(maxx - minx + 1)*scale_factor
    yspan = int(maxy - miny + 1)*scale_factor
    
    
    raster = np.zeros((xspan, yspan), dtype=bool)
    
    for x, y in get_coords(geometry):
        x_adj = int((x - minx)*scale_factor)
        y_adj = int((y - miny)*scale_factor)
        
        raster[x_adj, y_adj] = True
        
    return raster

In [9]:
def get_segment_lengths(geometry):
    polygons = get_polygons(geometry)
    lengths = []
    
    for p in polygons:
        coords = get_coords(p)
        for i, (x1, y1) in enumerate(coords):
            ni = i+1 if i+1 < len(coords) else 0
            x2, y2 = coords[ni]
            lengths.append(((x1-x2)**2+(y1-y2)**2)**0.5)
            
    return lengths

### Measurements:

Implemented:
 - Polsby-Popper
 - Convex Hull Area
 - Area
 - x/y symmetry
 - Variance in x/y coord
 - Boyce Clark

In [11]:
def polsby_popper(geometry):
    """Returns a number from 0 to 1, with 1 being the most compact"""
    
    return 4*math.pi*geometry.area/(geometry.length**2)

In [12]:
def convex_hull(geometry):
    """Returns the area of the convex hull of the geometry"""
    
    return geometry.convex_hull.area

In [13]:
def symmetry(geometry, y=False):
    """Calculates the symmetry as described by King"""
    x_t, y_t = (-1, 1) if y else (1,-1)
    reflected = shp.affinity.scale(geometry, xfact=x_t, yfact=y_t)
    intersect = reflected.intersection(geometry)
    
    return intersect.area / geometry.area

In [14]:
def long_variance(geometry):
    """Calculates the variance in longitude"""
    longs = [coord[0] for coord in get_coords(geometry)]
    return np.var(longs)

def lat_variance(geometry):
    """Calculates the variance in latitude"""
    lats = [coord[1] for coord in get_coords(geometry)]
    return np.var(lats)

In [15]:
# BUGGY
def significant_corners(geometry):
    """Calculates the number of significant corners"""
    raster = get_raster(test_geo, 10)
    cp = corner_peaks(corner_harris(raster), min_distance=1)
    return len(cp)

In [16]:
significant_corners(test_geo)

245

In [17]:
def length_variance(geometry):
    """Calculates the variance in segment length"""
    lengths = get_segment_lengths(geometry)
    return np.var(lengths)

In [18]:
length_variance(test_geo)

0.00064429681661958916

In [19]:
def boyce_clark(geometry):
    """Calculates the Boyce-Clark score of the district."""
    polygons = get_polygons(geometry)
    lengths = []
    for p in polygons:
        c_x, c_y = p.centroid.coords.xy
        c_x, c_y = c_x[0], c_y[0]
        
        for e_x, e_y in get_coords(p):
            lengths.append(((e_x-c_x)**2+(e_y-c_y)**2)**0.5)
            
    lengths = np.array(lengths)
    return 1/(2*mean(lengths))*mad(lengths)

In [20]:
boyce_clark(test_geo)

0.46679486649639296

### Vectorization

In [21]:
def make_vectorized(function):
    """Returns a wrapper function"""
    
    def wrapped(row):
        return function(row.geometry)
    
    return wrapped

In [22]:
pp = make_vectorized(polsby_popper)
ch = make_vectorized(convex_hull)
longv = make_vectorized(long_variance)
latv = make_vectorized(lat_variance)
sc = make_vectorized(significant_corners)
sv = make_vectorized(length_variance)
bc = make_vectorized(boyce_clark)
xsym = make_vectorized(symmetry)
ysym = make_vectorized(lambda x: symmetry(x, y=True))

In [23]:
data["PPopper"] = data.apply(pp, axis=1)
data["CHull"] = data.apply(ch, axis=1)
data["LongVar"] = data.apply(longv, axis=1)
data["LatVar"] = data.apply(latv, axis=1)
data["SigCorners"] = data.apply(sc, axis=1)
data["SegVar"] = data.apply(sv, axis=1)
data["BClark"] = data.apply(bc, axis=1)
data["XSym"] = data.apply(xsym, axis=1)
data["YSym"] = data.apply(ysym, axis=1)

### PCA

#### Visualization

In [30]:
measures = ["PPopper", "CHull","LongVar", "LatVar",  "SegVar", "BClark", "XSym", "YSym"]
graph_data = data[measures]
scale(graph_data, axis=1)

graph_data.head()

PPopper        CHull      LongVar     LatVar    SegVar    BClark  \
0  0.062121  3956.495031  7761.342779  28.894359  0.000644  0.466795   
1  0.492232     0.797959     0.024670   0.157386  0.000005  0.080282   
2  0.420380    48.445476    12.255949   2.204694  0.000009  0.097425   
3  0.433123    22.070344     4.239176   0.915248  0.000009  0.040033   
4  0.497700    24.337376     6.628116   1.501790  0.000010  0.080887   

       XSym      YSym  
0  0.416118  0.001522  
1  0.546937  0.636891  
2  0.800647  0.889581  
3  0.974389  0.950219  
4  0.840903  0.972283

In [34]:
fig = ff.create_scatterplotmatrix(graph_data, height=800, width=800)
iplot(fig, filename='Measures of Compactness')

In [47]:
sklearn_pca = PCA(n_components=2)
transformed = sklearn_pca.fit_transform(graph_data)

In [48]:
sklearn_pca.explained_variance_ratio_

array([  9.99910544e-01,   8.84538027e-05])

In [49]:
sklearn_pca.components_

array([[ -2.13547999e-05,   4.54012511e-01,   8.90989210e-01,
          3.29557842e-03,   7.31049776e-08,   3.80497772e-05,
         -2.02877536e-05,  -6.73141221e-05],
       [  5.11087858e-03,   8.86566822e-01,  -4.52119052e-01,
          9.74993170e-02,   5.47057778e-07,   1.12028801e-05,
          5.66087613e-03,   4.83205153e-03]])

In [59]:
trace = go.Scatter(
    x = transformed[:,0],
    y = transformed[:,1],
    mode = 'markers'
)

layout = go.Layout(xaxis=go.XAxis(title='PC1', showline=False),
                yaxis=go.YAxis(title='PC2', showline=False))
fig = go.Figure(data=[trace], layout=layout)
iplot(fig)